# Exercise PPM Part 2 - Small dataset

Imports

In [1]:
import pandas as pd

Import an event log as a pandas dataframe

In [2]:
df = pd.read_csv("Event_Logs/Sampled_BPIC17_offer_log.csv")
df

index           Case ID                  Activity  Resource  \
0          0   Offer_247135719            O_Create Offer   User_17   
1          1   Offer_247135719                 O_Created   User_17   
2          2   Offer_247135719      O_Sent (online only)   User_17   
3          3   Offer_247135719               O_Cancelled   User_17   
4          4   Offer_941964966            O_Create Offer   User_17   
...      ...               ...                       ...       ...   
22404  22404  Offer_1064426652            O_Create Offer   User_23   
22405  22405  Offer_1064426652                 O_Created   User_23   
22406  22406  Offer_1064426652  O_Sent (mail and online)   User_23   
22407  22407  Offer_1064426652                O_Returned  User_117   
22408  22408  Offer_1064426652                O_Accepted  User_102   

            Complete Timestamp    Variant  Variant index  (case) Accepted  \
0      2016/01/02 18:17:05.720  Variant 8              8             True   
1      2016/01/02 18:17:08.762  Variant 8              8             True   
2      2016/01/02 18:19:21.330  Variant 8              8             True   
3      2016/01/02 18:21:26.034  Variant 8              8             True   
4      2016/01/02 18:21:42.022  Variant 1              1             True   
...                        ...        ...            ...              ...   
22404  2016/02/18 22:50:01.446  Variant 2              2             True   
22405  2016/02/18 22:50:02.655  Variant 2              2             True   
22406  2016/02/18 22:50:22.174  Variant 2              2             True   
22407  2016/02/29 19:08:56.200  Variant 2              2             True   
22408  2016/02/29 23:43:45.831  Variant 2              2             True   

         (case) ApplicationID  (case) CreditScore  \
0       Application_196483749                   0   
1       Application_196483749                   0   
2       Application_196483749                   0   
3       Application_196483749                   0   
4       Application_196483749                   0   
...                       ...                 ...   
22404  Application_1574359134                 767   
22405  Application_1574359134                 767   
22406  Application_1574359134                 767   
22407  Application_1574359134                 767   
22408  Application_1574359134                 767   

       (case) FirstWithdrawalAmount  (case) MonthlyCost  (case) NumberOfTerms  \
0                           10000.0              201.76                    57   
1                           10000.0              201.76                    57   
2                           10000.0              201.76                    57   
3                           10000.0              201.76                    57   
4                            4100.0              201.76                    57   
...                             ...                 ...                   ...   
22404                        6000.0              118.56                    59   
22405                        6000.0              118.56                    59   
22406                        6000.0              118.56                    59   
22407                        6000.0              118.56                    59   
22408                        6000.0              118.56                    59   

       (case) OfferedAmount  (case) Selected       Action  \
0                   10000.0            False      Created   
1                   10000.0            False  statechange   
2                   10000.0            False  statechange   
3                   10000.0            False  statechange   
4                   10000.0            False      Created   
...                     ...              ...          ...   
22404                6000.0             True      Created   
22405                6000.0             True  statechange   
22406                6000.0             True  statechange   
22407                

Create an event log that retains only the attributes caseid, activity, timestamp, resource and outcome.

In [4]:
df = df.rename(columns={"Case ID":"caseid", "Activity":"activity", "Complete Timestamp":"ts", "Resource":"resource", "(case) Accepted":"outcome"})
df_2 = df[["caseid", "activity", "ts", "resource", "outcome"]].copy()
df_2

caseid                  activity                       ts  \
0       Offer_247135719            O_Create Offer  2016/01/02 18:17:05.720   
1       Offer_247135719                 O_Created  2016/01/02 18:17:08.762   
2       Offer_247135719      O_Sent (online only)  2016/01/02 18:19:21.330   
3       Offer_247135719               O_Cancelled  2016/01/02 18:21:26.034   
4       Offer_941964966            O_Create Offer  2016/01/02 18:21:42.022   
...                 ...                       ...                      ...   
22404  Offer_1064426652            O_Create Offer  2016/02/18 22:50:01.446   
22405  Offer_1064426652                 O_Created  2016/02/18 22:50:02.655   
22406  Offer_1064426652  O_Sent (mail and online)  2016/02/18 22:50:22.174   
22407  Offer_1064426652                O_Returned  2016/02/29 19:08:56.200   
22408  Offer_1064426652                O_Accepted  2016/02/29 23:43:45.831   

       resource  outcome  
0       User_17     True  
1       User_17     True  
2       User_17     True  
3       User_17     True  
4       User_17     True  
...         ...      ...  
22404   User_23     True  
22405   User_23     True  
22406   User_23     True  
22407  User_117     True  
22408  User_102     True  

[22409 rows x 5 columns]

 Create a function to extract the prefixes of length L from the event log.

In [50]:
import numpy as np
def create_prefix(df, L):
    res0 = df.sort_values(by=['caseid','ts']).groupby('caseid', as_index=False)['activity'].apply(list)    
    res1 = df.sort_values(by=['caseid','ts']).groupby('caseid', as_index=False)['ts'].apply(list)
    res2 = df.sort_values(by=['caseid','ts']).groupby('caseid', as_index=False)['resource'].apply(list)
    
    res = pd.merge(res0, pd.merge(res1, res2, on="caseid") , on="caseid")
    res["outcome"] = df["outcome"]
    
    event_num = df.groupby('caseid')['activity'].count().to_frame('event_number')
    res = pd.merge(res, event_num, on="caseid")
    
    res[res["event_number"] < L] = np.nan
    res = res.dropna()
    
    def function(row, label):
        activity_array = row[label][0:L]
        return activity_array
    
    for c in ["activity", "ts", "resource"]:
        res[c] = res.apply(lambda row: function(row, c), axis=1)
    
    res = res.drop(columns=["event_number"])
    return res
    

In [51]:
x = create_prefix(df, 3)
x

caseid                                           activity  \
0     Offer_1000681710  [O_Create Offer, O_Created, O_Sent (mail and o...   
1     Offer_1001553250  [O_Create Offer, O_Created, O_Sent (mail and o...   
2     Offer_1002136393  [O_Create Offer, O_Created, O_Sent (mail and o...   
3     Offer_1002236598  [O_Create Offer, O_Created, O_Sent (mail and o...   
4     Offer_1002530118  [O_Create Offer, O_Created, O_Sent (mail and o...   
...                ...                                                ...   
4995   Offer_993689039  [O_Create Offer, O_Created, O_Sent (mail and o...   
4996   Offer_993800442  [O_Create Offer, O_Created, O_Sent (mail and o...   
4997    Offer_99473283  [O_Create Offer, O_Created, O_Sent (mail and o...   
4998   Offer_995784215  [O_Create Offer, O_Created, O_Sent (mail and o...   
4999   Offer_997411923  [O_Create Offer, O_Created, O_Sent (mail and o...   

                                                     ts  \
0     [2016/02/02 18:24:54.170, 2016/02/02 18:24:55....   
1     [2016/01/16 03:16:41.868, 2016/01/16 03:16:43....   
2     [2016/01/29 17:46:49.529, 2016/01/29 17:46:50....   
3     [2016/01/12 18:24:55.557, 2016/01/12 18:24:56....   
4     [2016/02/17 02:25:07.160, 2016/02/17 02:25:08....   
...                                                 ...   
4995  [2016/01/29 18:34:42.819, 2016/01/29 18:34:44....   
4996  [2016/01/29 18:37:21.213, 2016/01/29 18:37:22....   
4997  [2016/02/03 20:59:31.775, 2016/02/03 20:59:33....   
4998  [2016/02/15 17:06:12.610, 2016/02/15 17:06:15....   
4999  [2016/01/02 20:25:44.202, 2016/01/02 20:25:45....   

                         resource  outcome  
0     [User_20, User_20, User_20]     True  
1        [User_2, User_2, User_2]     True  
2     [User_85, User_85, User_85]     True  
3     [User_49, User_49, User_49]     True  
4     [User_15, User_15, User_15]     True  
...                           ...      ...  
4995  [User_73, User_73, User_73]     True  
4996  [User_28, User_28, User_28]     True  
4997  [User_19, User_19, User_19]     True  
4998  [User_25, User_25, User_25]     True  
4999  [User_19, User_19, User_19]     True  

[5000 rows x 5 columns]

Create a function that does aggregation encoding of a prefix extracted from the event log

In [36]:
def one_hot(x, label, type):
    temp = []
    for element in x[label]:
        for e in element:
            temp.append(e)
            
    df = pd.DataFrame(temp)
    unique_val = df[0].unique()
    
    result = x[["caseid"]].copy()
    if type == "index":
        L = len(x[label][0]) # Length of the prefix
        for e in unique_val:
            for i in range(1, L+1): 
                result[label + "_" + str(i)+ "_" + e] = 0
        
        for index, row in x.iterrows():
            i = 1
            for activity in row[label]:
                result[label + "_" + str(i) + "_" + activity].iloc[index] += 1
                i += 1
        return result
    
    else:
        for e in unique_val:
            result[e] = 0
    
        for index, row in x.iterrows():
            for activity in row[label]:
                result[activity].iloc[index] += 1
    
    return result

def average_label(df, label):
    result = x[["caseid"]].copy()
    result["avg_"+label] = 0
    for index, row in df.iterrows():
        result["avg_" + label].iloc[index] = pd.to_datetime(row[label][-1]) - pd.to_datetime(row[label][0])
    return result


In [37]:
average_label(x, "ts")

/var/folders/76/2m87n1zs4352j9ydg5g8h8dc0000gn/T/ipykernel_54976/2197441255.py:38: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result["avg_" + label].iloc[index] = pd.to_datetime(row[label][-1]) - pd.to_datetime(row[label][0])
/var/folders/76/2m87n1zs4352j9ydg5g8h8dc0000gn/T/ipykernel_54976/2197441255.py:38: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '0 days 00:00:20.719000' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  result["avg_" + label].iloc[index] = pd.to_datetime(row[label][-1]) - pd.to_datetime(row[label][0])


caseid                  avg_ts
0     Offer_1000681710  0 days 00:00:20.719000
1     Offer_1001553250  0 days 00:00:16.660000
2     Offer_1002136393  0 days 00:00:20.849000
3     Offer_1002236598  0 days 00:00:12.617000
4     Offer_1002530118  0 days 00:00:21.234000
...                ...                     ...
4995   Offer_993689039  0 days 00:00:18.025000
4996   Offer_993800442  0 days 00:00:21.811000
4997    Offer_99473283  0 days 00:04:26.012000
4998   Offer_995784215  0 days 00:00:18.420000
4999   Offer_997411923  0 days 00:00:34.938000

[5000 rows x 2 columns]

In [38]:
one_hot(x, "activity", "aggr")

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



caseid  O_Create Offer  O_Created  O_Sent (mail and online)  \
0     Offer_1000681710               1          1                         1   
1     Offer_1001553250               1          1                         1   
2     Offer_1002136393               1          1                         1   
3     Offer_1002236598               1          1                         1   
4     Offer_1002530118               1          1                         1   
...                ...             ...        ...                       ...   
4995   Offer_993689039               1          1                         1   
4996   Offer_993800442               1          1                         1   
4997    Offer_99473283               1          1                         1   
4998   Offer_995784215               1          1                         1   
4999   Offer_997411923               1          1                         1   

      O_Sent (online only)  O_Cancelled  O_Refused  
0                        0            0          0  
1                        0            0          0  
2                        0            0          0  
3                        0            0          0  
4                        0            0          0  
...                    ...          ...        ...  
4995                     0            0          0  
4996                     0            0          0  
4997                     0            0          0  
4998                     0            0          0  
4999                     0            0          0  

[5000 rows x 7 columns]

In [39]:
one_hot(x, "resource", "aggr")

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



caseid  User_20  User_2  User_85  User_49  User_15  User_24  \
0     Offer_1000681710        3       0        0        0        0        0   
1     Offer_1001553250        0       3        0        0        0        0   
2     Offer_1002136393        0       0        3        0        0        0   
3     Offer_1002236598        0       0        0        3        0        0   
4     Offer_1002530118        0       0        0        0        3        0   
...                ...      ...     ...      ...      ...      ...      ...   
4995   Offer_993689039        0       0        0        0        0        0   
4996   Offer_993800442        0       0        0        0        0        0   
4997    Offer_99473283        0       0        0        0        0        0   
4998   Offer_995784215        0       0        0        0        0        0   
4999   Offer_997411923        0       0        0        0        0        0   

      User_18  User_27  User_16  ...  User_101  User_76  User_119  User_117  \
0           0        0        0  ...         0        0         0         0   
1           0        0        0  ...         0        0         0         0   
2           0        0        0  ...         0        0         0         0   
3           0        0        0  ...         0        0         0         0   
4           0        0        0  ...         0        0         0         0   
...       ...      ...      ...  ...       ...      ...       ...       ...   
4995        0        0        0  ...         0        0         0         0   
4996        0        0        0  ...         0        0         0         0   
4997        0        0        0  ...         0        0         0         0   
4998        0        0        0  ...         0        0         0         0   
4999        0        0        0  ...         0        0         0         0   

      User_99  User_112  User_100  User_116  User_30  User_113  
0           0         0         0         0        0         0  
1           0         0         0         0        0         0  
2           0         0         0         0        0         0  
3           0         0         0         0        0         0  
4           0         0         0         0        0         0  
...       ...       ...       ...       ...      ...       ...  
4995        0         0         0         0        0         0  
4996        0         0         0         0        0         0  
4997        0         0         0         0        0         0  
4998        0         0         0         0        0         0  
4999        0         0         0         0        0         0  

[5000 rows x 71 columns]

In [54]:
def aggregation_enc(df):
    res0 = one_hot(df, "activity", "aggr")
    res1 = one_hot(df, "resource", "aggr")
    res2 = average_label(df, "ts")
    
    res = pd.merge(res0, pd.merge(res1, res2), on="caseid")
    
    res["outcome"] = df["outcome"]

    return res

In [55]:
aggregation_enc(x)

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)

/var/folders/76/2m87n1zs4352j9ydg5g8h8dc0000gn/T/ipykernel_54976/2197441255.py:30: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result[activity].iloc[index] += 1
/var/folders/76/2m87n1zs4352j9ydg5g8h8dc0000gn/T/ipykernel_54976/2197441255.py:30: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result[activi

caseid  O_Create Offer  O_Created  O_Sent (mail and online)  \
0     Offer_1000681710               1          1                         1   
1     Offer_1001553250               1          1                         1   
2     Offer_1002136393               1          1                         1   
3     Offer_1002236598               1          1                         1   
4     Offer_1002530118               1          1                         1   
...                ...             ...        ...                       ...   
4995   Offer_993689039               1          1                         1   
4996   Offer_993800442               1          1                         1   
4997    Offer_99473283               1          1                         1   
4998   Offer_995784215               1          1                         1   
4999   Offer_997411923               1          1                         1   

      O_Sent (online only)  O_Cancelled  O_Refused  User_20  User_2  User_85  \
0                        0            0          0        3       0        0   
1                        0            0          0        0       3        0   
2                        0            0          0        0       0        3   
3                        0            0          0        0       0        0   
4                        0            0          0        0       0        0   
...                    ...          ...        ...      ...     ...      ...   
4995                     0            0          0        0       0        0   
4996                     0            0          0        0       0        0   
4997                     0            0          0        0       0        0   
4998                     0            0          0        0       0        0   
4999                     0            0          0        0       0        0   

      ...  User_119  User_117  User_99  User_112  User_100  User_116  User_30  \
0     ...         0         0        0         0         0         0        0   
1     ...         0         0        0         0         0         0        0   
2     ...         0         0        0         0         0         0        0   
3     ...         0         0        0         0         0         0        0   
4     ...         0         0        0         0         0         0        0   
...   ...       ...       ...      ...       ...       ...       ...      ...   
4995  ...         0         0        0         0         0         0        0   
4996  ...         0         0        0         0         0         0        0   
4997  ...         0         0        0         0         0         0        0   
4998  ...         0         0        0         0         0         0        0   
4999  ...         0         0        0         0         0         0        0   

      User_113                  avg_ts  outcome  
0            0  0 days 00:00:20.719000     True  
1            0  0 days 00:00:16.660000     True  
2            0  0 days 00:00:20.849000     True  
3            0  0 days 00:00:12.617000     True  
4            0  0 days 00:00:21.234000     True  
...        ...                     ...      ...  
4995         0  0 days 00:00:18.025000     True  
4996         0  0 days 00:00:21.811000     True  
4997         0  0 days 00:04:26.012000     True  
4998         0  0 days 00:00:18.420000     True  
4999         0  0 days 00:00:34.938000     True  

[5000 rows x 79 columns]

Create a function that does index-based encoding of a prefix extracted from the event log.

In [42]:
def index_label(df, label):
    L = len(df[label][0])
    result = x[["caseid"]].copy()
    
    # Create the column and put them to 0
    for i in range(1, L+1):
        result[label + "_" + str(i)] = 0
        
    for index, row in x.iterrows():
        i = 1
        for element in row[label]:
            result[label + "_" + str(i)].iloc[index] = element
            i += 1
    
    return result

In [43]:
one_hot(x, "activity", "index")

/var/folders/76/2m87n1zs4352j9ydg5g8h8dc0000gn/T/ipykernel_54976/2197441255.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result[label + "_" + str(i) + "_" + activity].iloc[index] += 1
/var/folders/76/2m87n1zs4352j9ydg5g8h8dc0000gn/T/ipykernel_54976/2197441255.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result[label + "_" + str(i) + "_" + activity].iloc[index] += 1
/var/folders/76/2m87n1zs4352j9ydg5g8h8dc0000gn/T/ipykernel_54976/2197441255.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pan

caseid  activity_1_O_Create Offer  activity_2_O_Create Offer  \
0     Offer_1000681710                          1                          0   
1     Offer_1001553250                          1                          0   
2     Offer_1002136393                          1                          0   
3     Offer_1002236598                          1                          0   
4     Offer_1002530118                          1                          0   
...                ...                        ...                        ...   
4995   Offer_993689039                          1                          0   
4996   Offer_993800442                          1                          0   
4997    Offer_99473283                          1                          0   
4998   Offer_995784215                          1                          0   
4999   Offer_997411923                          1                          0   

      activity_3_O_Create Offer  activity_1_O_Created  activity_2_O_Created  \
0                             0                     0                     1   
1                             0                     0                     1   
2                             0                     0                     1   
3                             0                     0                     1   
4                             0                     0                     1   
...                         ...                   ...                   ...   
4995                          0                     0                     1   
4996                          0                     0                     1   
4997                          0                     0                     1   
4998                          0                     0                     1   
4999                          0                     0                     1   

      activity_3_O_Created  activity_1_O_Sent (mail and online)  \
0                        0                                    0   
1                        0                                    0   
2                        0                                    0   
3                        0                                    0   
4                        0                                    0   
...                    ...                                  ...   
4995                     0                                    0   
4996                     0                                    0   
4997                     0                                    0   
4998                     0                                    0   
4999                     0                                    0   

      activity_2_O_Sent (mail and online)  \
0                                       0   
1                                       0   
2                                       0   
3                                       0   
4                                       0   
...                                   ...   
4995                                    0   
4996                                    0   
4997                                    0   
4998                                    0   
4999                                    0   

      activity_3_O_Sent (mail and online)  activity_1_O_Sent (online only)  \
0                                       1                                0   
1                                       1                                0   
2                                       1                                0   
3                                       1                                0   
4                                       1                                0   
...                                   ...                              ...   
4995                                    1                                0   
4996                                    1                                0   
4997                                    1                 

In [44]:
one_hot(x, "resource", "index")

/var/folders/76/2m87n1zs4352j9ydg5g8h8dc0000gn/T/ipykernel_54976/2197441255.py:15: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  result[label + "_" + str(i)+ "_" + e] = 0
/var/folders/76/2m87n1zs4352j9ydg5g8h8dc0000gn/T/ipykernel_54976/2197441255.py:15: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  result[label + "_" + str(i)+ "_" + e] = 0
/var/folders/76/2m87n1zs4352j9ydg5g8h8dc0000gn/T/ipykernel_54976/2197441255.py:15: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` man

caseid  resource_1_User_20  resource_2_User_20  \
0     Offer_1000681710                   1                   1   
1     Offer_1001553250                   0                   0   
2     Offer_1002136393                   0                   0   
3     Offer_1002236598                   0                   0   
4     Offer_1002530118                   0                   0   
...                ...                 ...                 ...   
4995   Offer_993689039                   0                   0   
4996   Offer_993800442                   0                   0   
4997    Offer_99473283                   0                   0   
4998   Offer_995784215                   0                   0   
4999   Offer_997411923                   0                   0   

      resource_3_User_20  resource_1_User_2  resource_2_User_2  \
0                      1                  0                  0   
1                      0                  1                  1   
2                      0                  0                  0   
3                      0                  0                  0   
4                      0                  0                  0   
...                  ...                ...                ...   
4995                   0                  0                  0   
4996                   0                  0                  0   
4997                   0                  0                  0   
4998                   0                  0                  0   
4999                   0                  0                  0   

      resource_3_User_2  resource_1_User_85  resource_2_User_85  \
0                     0                   0                   0   
1                     1                   0                   0   
2                     0                   1                   1   
3                     0                   0                   0   
4                     0                   0                   0   
...                 ...                 ...                 ...   
4995                  0                   0                   0   
4996                  0                   0                   0   
4997                  0                   0                   0   
4998                  0                   0                   0   
4999                  0                   0                   0   

      resource_3_User_85  ...  resource_3_User_100  resource_1_User_116  \
0                      0  ...                    0                    0   
1                      0  ...                    0                    0   
2                      1  ...                    0                    0   
3                      0  ...                    0                    0   
4                      0  ...                    0                    0   
...                  ...  ...                  ...                  ...   
4995                   0  ...                    0                    0   
4996                   0  ...                    0                    0   
4997                   0  ...                    0                    0   
4998                   0  ...                    0                    0   
4999                   0  ...                    0                    0   

      resource_2_User_116  resource_3_User_116  resource_1_User_30  \
0                       0                    0                   0   
1                       0                    0                   0   
2                       0                    0                   0   
3                       0                    0                   0   
4                       0                    0                   0   
...                   ...                  ...                 ...   
4995                    0                    0                   0   
4996                    0                    0                   0   
4997                    0                    0                   0   
4998                    

In [45]:
index_label(x, "ts")

/var/folders/76/2m87n1zs4352j9ydg5g8h8dc0000gn/T/ipykernel_54976/401174132.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result[label + "_" + str(i)].iloc[index] = element
/var/folders/76/2m87n1zs4352j9ydg5g8h8dc0000gn/T/ipykernel_54976/401174132.py:12: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '2016/02/02 18:24:54.170' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  result[label + "_" + str(i)].iloc[index] = element
/var/folders/76/2m87n1zs4352j9ydg5g8h8dc0000gn/T/ipykernel_54976/401174132.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/i

caseid                     ts_1                     ts_2  \
0     Offer_1000681710  2016/02/02 18:24:54.170  2016/02/02 18:24:55.833   
1     Offer_1001553250  2016/01/16 03:16:41.868  2016/01/16 03:16:43.056   
2     Offer_1002136393  2016/01/29 17:46:49.529  2016/01/29 17:46:50.822   
3     Offer_1002236598  2016/01/12 18:24:55.557  2016/01/12 18:24:56.826   
4     Offer_1002530118  2016/02/17 02:25:07.160  2016/02/17 02:25:08.376   
...                ...                      ...                      ...   
4995   Offer_993689039  2016/01/29 18:34:42.819  2016/01/29 18:34:44.881   
4996   Offer_993800442  2016/01/29 18:37:21.213  2016/01/29 18:37:22.743   
4997    Offer_99473283  2016/02/03 20:59:31.775  2016/02/03 20:59:33.058   
4998   Offer_995784215  2016/02/15 17:06:12.610  2016/02/15 17:06:15.203   
4999   Offer_997411923  2016/01/02 20:25:44.202  2016/01/02 20:25:45.416   

                         ts_3  
0     2016/02/02 18:25:14.889  
1     2016/01/16 03:16:58.528  
2     2016/01/29 17:47:10.378  
3     2016/01/12 18:25:08.174  
4     2016/02/17 02:25:28.394  
...                       ...  
4995  2016/01/29 18:35:00.844  
4996  2016/01/29 18:37:43.024  
4997  2016/02/03 21:03:57.787  
4998  2016/02/15 17:06:31.030  
4999  2016/01/02 20:26:19.140  

[5000 rows x 4 columns]

In [52]:
def index_enc(df):
    res0 = one_hot(df, "activity", "index")
    res1 = one_hot(df, "resource", "index")
    res2 = index_label(df, "ts")
    
    res = pd.merge(res0, pd.merge(res1, res2), on="caseid")
    
    res["outcome"] = df["outcome"]
    
    return res

In [53]:
index_enc(x)

/var/folders/76/2m87n1zs4352j9ydg5g8h8dc0000gn/T/ipykernel_54976/2197441255.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result[label + "_" + str(i) + "_" + activity].iloc[index] += 1
/var/folders/76/2m87n1zs4352j9ydg5g8h8dc0000gn/T/ipykernel_54976/2197441255.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result[label + "_" + str(i) + "_" + activity].iloc[index] += 1
/var/folders/76/2m87n1zs4352j9ydg5g8h8dc0000gn/T/ipykernel_54976/2197441255.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pan

caseid  activity_1_O_Create Offer  activity_2_O_Create Offer  \
0     Offer_1000681710                          1                          0   
1     Offer_1001553250                          1                          0   
2     Offer_1002136393                          1                          0   
3     Offer_1002236598                          1                          0   
4     Offer_1002530118                          1                          0   
...                ...                        ...                        ...   
4995   Offer_993689039                          1                          0   
4996   Offer_993800442                          1                          0   
4997    Offer_99473283                          1                          0   
4998   Offer_995784215                          1                          0   
4999   Offer_997411923                          1                          0   

      activity_3_O_Create Offer  activity_1_O_Created  activity_2_O_Created  \
0                             0                     0                     1   
1                             0                     0                     1   
2                             0                     0                     1   
3                             0                     0                     1   
4                             0                     0                     1   
...                         ...                   ...                   ...   
4995                          0                     0                     1   
4996                          0                     0                     1   
4997                          0                     0                     1   
4998                          0                     0                     1   
4999                          0                     0                     1   

      activity_3_O_Created  activity_1_O_Sent (mail and online)  \
0                        0                                    0   
1                        0                                    0   
2                        0                                    0   
3                        0                                    0   
4                        0                                    0   
...                    ...                                  ...   
4995                     0                                    0   
4996                     0                                    0   
4997                     0                                    0   
4998                     0                                    0   
4999                     0                                    0   

      activity_2_O_Sent (mail and online)  \
0                                       0   
1                                       0   
2                                       0   
3                                       0   
4                                       0   
...                                   ...   
4995                                    0   
4996                                    0   
4997                                    0   
4998                                    0   
4999                                    0   

      activity_3_O_Sent (mail and online)  ...  resource_1_User_30  \
0                                       1  ...                   0   
1                                       1  ...                   0   
2                                       1  ...                   0   
3                                       1  ...                   0   
4                                       1  ...                   0   
...                                   ...  ...                 ...   
4995                                    1  ...                   0   
4996                                    1  ...                   0   
4997                                    1  ...                   0   
4998                                    1  ...              